In [1]:
import pandas as pd
import numpy as np
from collections import defaultdict
import sys

In [2]:
movie_name_data = pd.read_csv("files/movies.csv",
                     names=["MOVIE_ID","TITLE","GENRES"],header=1)
all_ratings = pd.read_csv("files/ratings.csv",
                      names=["USER_ID","MOVIE_ID","RATING","TIMESTAMP"],header=1)

In [3]:
all_ratings["FAVORABLE"]=all_ratings["RATING"]>3
ratings=all_ratings[all_ratings["USER_ID"].isin(range(200))]

In [4]:
favorable_ratings = ratings[ratings["FAVORABLE"]]

In [5]:
favorable_reviews_by_users = dict((k, frozenset(v.values)) for k, v in favorable_ratings.groupby("USER_ID")["MOVIE_ID"])

In [6]:
num_favorable_by_movie = ratings[["MOVIE_ID", "FAVORABLE"]].groupby("MOVIE_ID").sum()

In [7]:
def find_frequent_itemsets(favorable_reviews_by_users, k_1_itemsets, min_support):
    counts = defaultdict(int)
    for user, reviews in favorable_reviews_by_users.items():
        for itemset in k_1_itemsets:
            if itemset.issubset(reviews):
                for other_reviewed_movie in reviews - itemset:
                    current_superset = itemset | frozenset((other_reviewed_movie,))
                    counts[current_superset] += 1
    return dict([(itemset, frequency) for itemset, frequency in counts.items() if frequency >= min_support])

In [8]:
frequent_itemsets = {}  # itemsets are sorted by length
min_support = 50

# k=1 candidates are the isbns with more than min_support favourable reviews
frequent_itemsets[1] = dict((frozenset((movie_id,)), row["FAVORABLE"])
                                for movie_id, row in num_favorable_by_movie.iterrows()
                                if row["FAVORABLE"] > min_support)

for k in range(2, 20):
    # Generate candidates of length k, using the frequent itemsets of length k-1
    # Only store the frequent itemsets
    cur_frequent_itemsets = find_frequent_itemsets(favorable_reviews_by_users, frequent_itemsets[k-1],
                                                   min_support)
    if len(cur_frequent_itemsets) == 0:
        break
    else:
        frequent_itemsets[k] = cur_frequent_itemsets
# We aren't interested in the itemsets of length 1, so remove those
del frequent_itemsets[1]

In [9]:
# Now we create the association rules. First, they are candidates until the confidence has been tested
candidate_rules = []
for itemset_length, itemset_counts in frequent_itemsets.items():
    for itemset in itemset_counts.keys():
        for conclusion in itemset:
            premise = itemset - set((conclusion,))
            candidate_rules.append((premise, conclusion))

In [10]:
# Now, we compute the confidence of each of these rules. This is very similar to what we did in chapter 1
correct_counts = defaultdict(int)
incorrect_counts = defaultdict(int)
for user, reviews in favorable_reviews_by_users.items():
    for candidate_rule in candidate_rules:
        premise, conclusion = candidate_rule
        if premise.issubset(reviews):
            if conclusion in reviews:
                correct_counts[candidate_rule] += 1
            else:
                incorrect_counts[candidate_rule] += 1
rule_confidence = {candidate_rule: correct_counts[candidate_rule] / float(correct_counts[candidate_rule] + incorrect_counts[candidate_rule])
              for candidate_rule in candidate_rules}

In [11]:
# Choose only rules above a minimum confidence level
min_confidence = 0.1

In [12]:
# Filter out the rules with poor confidence
rule_confidence = {rule: confidence for rule, confidence in rule_confidence.items() if confidence > min_confidence}

In [13]:
from operator import itemgetter
sorted_confidence = sorted(rule_confidence.items(), key=itemgetter(1), reverse=True)

In [14]:
sorted_confidence

[((frozenset({47, 260, 527}), 2571), 1.0),
 ((frozenset({47, 260, 2858}), 2571), 1.0),
 ((frozenset({47, 260, 356}), 2571), 1.0),
 ((frozenset({50, 1196, 1210}), 260), 1.0),
 ((frozenset({1196, 1210, 2571}), 260), 1.0),
 ((frozenset({1198, 1210, 2571}), 260), 1.0),
 ((frozenset({260, 2028, 2858}), 2571), 1.0),
 ((frozenset({593, 1196, 1198}), 260), 1.0),
 ((frozenset({593, 1196, 1210}), 260), 1.0),
 ((frozenset({593, 1198, 1210}), 260), 1.0),
 ((frozenset({356, 1196, 1198}), 260), 1.0),
 ((frozenset({1196, 1198, 2028}), 260), 1.0),
 ((frozenset({1196, 1210, 2858}), 260), 1.0),
 ((frozenset({356, 1196, 1210}), 260), 1.0),
 ((frozenset({356, 1198, 1210}), 260), 1.0),
 ((frozenset({1198, 1210, 2028}), 260), 1.0),
 ((frozenset({356, 1196, 2028}), 2571), 1.0),
 ((frozenset({527, 1198, 2028}), 2571), 1.0),
 ((frozenset({47, 296, 590}), 593), 1.0),
 ((frozenset({858, 1196, 2571}), 260), 1.0),
 ((frozenset({296, 1196, 1198}), 260), 1.0),
 ((frozenset({318, 1196, 1198}), 260), 1.0),
 ((frozense

In [15]:
def get_movie_name(movie_id):
    title_object = movie_name_data[movie_name_data["MOVIE_ID"] == movie_id]["TITLE"]
    title = title_object.values[0]
    return title

In [16]:
lista=['Star Wars: Episode IV - A New Hope (1977)', ' Seven (a.k.a. Se7en) (1995)', " Schindler's List (1993)"]

for index in range(len(sorted_confidence)):
    (premise, conclusion) = sorted_confidence[index][0]
    premise_names = ", ".join(get_movie_name(idx) for idx in premise)
    my_list = premise_names.split(",")
        
        
    conclusion_name = get_movie_name(conclusion)
    print("Given that you like the following movie(s):\n")
    print("{0}".format(premise_names))
    print("\n")
    print("You will surely like:\n")
    print("{0}".format(conclusion_name))
    print("")

Given that you like the following movie(s):

Star Wars: Episode IV - A New Hope (1977), Seven (a.k.a. Se7en) (1995), Schindler's List (1993)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

American Beauty (1999), Star Wars: Episode IV - A New Hope (1977), Seven (a.k.a. Se7en) (1995)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Forrest Gump (1994), Star Wars: Episode IV - A New Hope (1977), Seven (a.k.a. Se7en) (1995)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Star Wars: Episode VI - Return of the Jedi (1983), Usual Suspects, The (1995), Star Wars: Episode V - The Empire Strikes Back (1980)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Star Wars: Episode VI - Return of the Jedi (1983), Matrix, The (1999), Star Wars: Episode V - The Empire Strikes Back (1980)


You will surely like:

Star W

Given that you like the following movie(s):

Forrest Gump (1994), Star Wars: Episode IV - A New Hope (1977), Braveheart (1995), Schindler's List (1993)


You will surely like:

Silence of the Lambs, The (1991)

Given that you like the following movie(s):

Star Wars: Episode IV - A New Hope (1977), Schindler's List (1993), Saving Private Ryan (1998), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Silence of the Lambs, The (1991), Matrix, The (1999), Star Wars: Episode V - The Empire Strikes Back (1980), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Silence of the Lambs, The (1991), Star Wars: Episode VI - Return of the Jedi (1983), Matrix, The (1999), Star Wars: Episode V - The Empire Strikes Back (1980)


You will surely l

Given that you like the following movie(s):

Forrest Gump (1994), Star Wars: Episode IV - A New Hope (1977), Shawshank Redemption, The (1994), Seven (a.k.a. Se7en) (1995)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Godfather, The (1972), Matrix, The (1999), Forrest Gump (1994), Schindler's List (1993)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Pulp Fiction (1994), Star Wars: Episode IV - A New Hope (1977), Saving Private Ryan (1998), Schindler's List (1993)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Godfather, The (1972), Matrix, The (1999), Saving Private Ryan (1998), Schindler's List (1993)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Pulp Fiction (1994), Matrix, The (1999), Star Wars: Episode V - The Empire Strikes Back (1980), Raiders of the Lost Ark (Ind

Given that you like the following movie(s):

Pulp Fiction (1994), American Beauty (1999), Forrest Gump (1994), Saving Private Ryan (1998)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Pulp Fiction (1994), Saving Private Ryan (1998), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981), Schindler's List (1993)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Saving Private Ryan (1998), Schindler's List (1993), Shawshank Redemption, The (1994), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Godfather, The (1972), Saving Private Ryan (1998), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981), Schindler's List (1993)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Godfather, The (1972), Savin

Given that you like the following movie(s):

Pulp Fiction (1994), Godfather, The (1972), Forrest Gump (1994), Schindler's List (1993)


You will surely like:

Shawshank Redemption, The (1994)

Given that you like the following movie(s):

Pulp Fiction (1994), Godfather, The (1972), Star Wars: Episode IV - A New Hope (1977), Terminator 2: Judgment Day (1991)


You will surely like:

Matrix, The (1999)

Given that you like the following movie(s):

Pulp Fiction (1994), Godfather, The (1972), Star Wars: Episode V - The Empire Strikes Back (1980), Shawshank Redemption, The (1994)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Pulp Fiction (1994), Godfather, The (1972), Star Wars: Episode V - The Empire Strikes Back (1980), Terminator 2: Judgment Day (1991)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Star Wars: Episode VI - Return of the Jedi (1983), Star Wars

...

Given that you like the following movie(s):

Pulp Fiction (1994), American Beauty (1999)


You will surely like:

Star Wars: Episode V - The Empire Strikes Back (1980)

Given that you like the following movie(s):

Pulp Fiction (1994), American Beauty (1999)


You will surely like:

Saving Private Ryan (1998)

Given that you like the following movie(s):

Pulp Fiction (1994), Braveheart (1995)


You will surely like:

Star Wars: Episode VI - Return of the Jedi (1983)

Given that you like the following movie(s):

Pulp Fiction (1994), Braveheart (1995)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Silence of the Lambs, The (1991), Godfather, The (1972)


You will surely like:

Saving Private Ryan (1998)

Given that you like the following movie(s):

Silence of the Lambs, The (1991), Godfather, The (1972)


You will surely like:

Terminator 2: Judgment Day (1991)

Given that you like the following movie(s):

Silence of the La

Given that you like the following movie(s):

Forrest Gump (1994), Shawshank Redemption, The (1994), Seven (a.k.a. Se7en) (1995)


You will surely like:

Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)

Given that you like the following movie(s):

Forrest Gump (1994), Shawshank Redemption, The (1994), Seven (a.k.a. Se7en) (1995)


You will surely like:

Star Wars: Episode IV - A New Hope (1977)

Given that you like the following movie(s):

Forrest Gump (1994), Shawshank Redemption, The (1994), Seven (a.k.a. Se7en) (1995)


You will surely like:

American Beauty (1999)

Given that you like the following movie(s):

Star Wars: Episode V - The Empire Strikes Back (1980), Star Wars: Episode IV - A New Hope (1977), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)


You will surely like:

Shawshank Redemption, The (1994)

Given that you like the following movie(s):

Forrest Gump (1994), Shawshank Redemption, The (1994), Saving Privat

Given that you like the following movie(s):

Pulp Fiction (1994), Silence of the Lambs, The (1991), Forrest Gump (1994), Shawshank Redemption, The (1994)


You will surely like:

Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)

Given that you like the following movie(s):

Seven (a.k.a. Se7en) (1995)


You will surely like:

Dances with Wolves (1990)

Given that you like the following movie(s):

Silence of the Lambs, The (1991), Braveheart (1995), Shawshank Redemption, The (1994)


You will surely like:

Star Wars: Episode VI - Return of the Jedi (1983)

Given that you like the following movie(s):

Pulp Fiction (1994), Silence of the Lambs, The (1991), Godfather, The (1972)


You will surely like:

Terminator 2: Judgment Day (1991)

Given that you like the following movie(s):

Pulp Fiction (1994), Silence of the Lambs, The (1991), Godfather, The (1972)


You will surely like:

Saving Private Ryan (1998)

Given that you like the following movie(s):

Pulp Fi

Given that you like the following movie(s):

Pulp Fiction (1994), Forrest Gump (1994)


You will surely like:

American Beauty (1999)

Given that you like the following movie(s):

Matrix, The (1999), Star Wars: Episode IV - A New Hope (1977), Raiders of the Lost Ark (Indiana Jones and the Raiders of the Lost Ark) (1981)


You will surely like:

Fargo (1996)

Given that you like the following movie(s):

Matrix, The (1999), Forrest Gump (1994), Shawshank Redemption, The (1994)


You will surely like:

Fargo (1996)

Given that you like the following movie(s):

Pulp Fiction (1994), Usual Suspects, The (1995), Shawshank Redemption, The (1994)


You will surely like:

Braveheart (1995)

Given that you like the following movie(s):

Braveheart (1995), Forrest Gump (1994), Shawshank Redemption, The (1994)


You will surely like:

Apollo 13 (1995)

Given that you like the following movie(s):

Pulp Fiction (1994), Shawshank Redemption, The (1994), Seven (a.k.a. Se7en) (1995)


You will surely lik


Braveheart (1995)


You will surely like:

Usual Suspects, The (1995)

Given that you like the following movie(s):

Braveheart (1995)


You will surely like:

Star Wars: Episode V - The Empire Strikes Back (1980)

Given that you like the following movie(s):

Forrest Gump (1994)


You will surely like:

Seven (a.k.a. Se7en) (1995)

Given that you like the following movie(s):

Forrest Gump (1994)


You will surely like:

Saving Private Ryan (1998)

Given that you like the following movie(s):

Pulp Fiction (1994), Forrest Gump (1994)


You will surely like:

Star Wars: Episode V - The Empire Strikes Back (1980)

Given that you like the following movie(s):

Pulp Fiction (1994), Forrest Gump (1994)


You will surely like:

Fargo (1996)

Given that you like the following movie(s):

Star Wars: Episode IV - A New Hope (1977)


You will surely like:

Schindler's List (1993)

Given that you like the following movie(s):

Pulp Fiction (1994)


You will surely like:

Star Wars: Episode V - The Emp

In [17]:
sorted_confidence

[((frozenset({47, 260, 527}), 2571), 1.0),
 ((frozenset({47, 260, 2858}), 2571), 1.0),
 ((frozenset({47, 260, 356}), 2571), 1.0),
 ((frozenset({50, 1196, 1210}), 260), 1.0),
 ((frozenset({1196, 1210, 2571}), 260), 1.0),
 ((frozenset({1198, 1210, 2571}), 260), 1.0),
 ((frozenset({260, 2028, 2858}), 2571), 1.0),
 ((frozenset({593, 1196, 1198}), 260), 1.0),
 ((frozenset({593, 1196, 1210}), 260), 1.0),
 ((frozenset({593, 1198, 1210}), 260), 1.0),
 ((frozenset({356, 1196, 1198}), 260), 1.0),
 ((frozenset({1196, 1198, 2028}), 260), 1.0),
 ((frozenset({1196, 1210, 2858}), 260), 1.0),
 ((frozenset({356, 1196, 1210}), 260), 1.0),
 ((frozenset({356, 1198, 1210}), 260), 1.0),
 ((frozenset({1198, 1210, 2028}), 260), 1.0),
 ((frozenset({356, 1196, 2028}), 2571), 1.0),
 ((frozenset({527, 1198, 2028}), 2571), 1.0),
 ((frozenset({47, 296, 590}), 593), 1.0),
 ((frozenset({858, 1196, 2571}), 260), 1.0),
 ((frozenset({296, 1196, 1198}), 260), 1.0),
 ((frozenset({318, 1196, 1198}), 260), 1.0),
 ((frozense

In [32]:
list(set(movie_name_data["TITLE"]))[:50]

['Cecil B. DeMented (2000)',
 'While You Were Fighting: A Thor Mockumentary (2016)',
 'Johnny Mnemonic (1995)',
 'From Justin to Kelly (2003)',
 'Ghost Town (2008)',
 "'Salem's Lot (2004)",
 'Boxcar Bertha (1972)',
 'Death at a Funeral (2010)',
 'Dirty Harry (1971)',
 "Legend of 1900, The (a.k.a. The Legend of the Pianist on the Ocean) (Leggenda del pianista sull'oceano) (1998)",
 'Private Eyes, The (1981)',
 'Shrek the Halls (2007)',
 'Masquerade (1988)',
 'Riding in Cars with Boys (2001)',
 'Armour of God (Long xiong hu di) (1987)',
 'For the Birds (2000)',
 'Love and Death on Long Island (1997)',
 'Zombie Strippers! (2008)',
 'Mamma Mia: Here We Go Again! (2018)',
 'Paulie (1998)',
 'Hunt For Gollum, The (2009)',
 'Cobra (1986)',
 'Libertine, The (2004)',
 'Sure Thing, The (1985)',
 'Eulogy (2004)',
 'Mighty Heart, A (2007)',
 'Jane Eyre (1970)',
 'Memphis Belle (1990)',
 'Ref, The (1994)',
 'Arrival (2016)',
 'Superman II (1980)',
 'American Pie Presents Beta House (American Pie 6:

In [27]:
[[x,list(set(movie_name_data["TITLE"])).count] for x in set(movie_name_data["TITLE"])]

[['Cecil B. DeMented (2000)', <function list.count(value, /)>],
 ['While You Were Fighting: A Thor Mockumentary (2016)',
  <function list.count(value, /)>],
 ['Johnny Mnemonic (1995)', <function list.count(value, /)>],
 ['From Justin to Kelly (2003)', <function list.count(value, /)>],
 ['Ghost Town (2008)', <function list.count(value, /)>],
 ["'Salem's Lot (2004)", <function list.count(value, /)>],
 ['Boxcar Bertha (1972)', <function list.count(value, /)>],
 ['Death at a Funeral (2010)', <function list.count(value, /)>],
 ['Dirty Harry (1971)', <function list.count(value, /)>],
 ["Legend of 1900, The (a.k.a. The Legend of the Pianist on the Ocean) (Leggenda del pianista sull'oceano) (1998)",
  <function list.count(value, /)>],
 ['Private Eyes, The (1981)', <function list.count(value, /)>],
 ['Shrek the Halls (2007)', <function list.count(value, /)>],
 ['Masquerade (1988)', <function list.count(value, /)>],
 ['Riding in Cars with Boys (2001)', <function list.count(value, /)>],
 ['Armour